In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.vocab

OrderedDict([('0', 0),
             ('1', 1),
             ('2', 2),
             ('3', 3),
             ('4', 4),
             ('5', 5),
             ('6', 6),
             ('7', 7),
             ('8', 8),
             ('9', 9),
             ('10', 10),
             ('11', 11),
             ('12', 12),
             ('13', 13),
             ('14', 14),
             ('15', 15),
             ('16', 16),
             ('17', 17),
             ('18', 18),
             ('19', 19),
             ('20', 20),
             ('21', 21),
             ('22', 22),
             ('23', 23),
             ('24', 24),
             ('25', 25),
             ('26', 26),
             ('27', 27),
             ('28', 28),
             ('29', 29),
             ('30', 30),
             ('31', 31),
             ('32', 32),
             ('33', 33),
             ('34', 34),
             ('35', 35),
             ('36', 36),
             ('37', 37),
             ('38', 38),
             ('39', 39),
             ('40', 

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]

In [ ]:
decode_tokenizer.vocab_size

302

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

In [ ]:
text_id_output.logits


tensor([[[ 2.9446e-01, -3.6372e-02, -7.5298e-01, -7.2680e-02, -7.6963e-02,
          -1.2474e-01, -5.1587e-01, -1.8860e-01, -6.2553e-01,  2.3972e-01,
          -3.7170e-01,  5.1379e-01,  1.8448e-01,  3.3394e-01,  3.4073e-01,
           1.6973e-01, -2.8505e-01, -5.0863e-01,  1.0504e+00, -6.5665e-02,
           1.2553e+00,  4.9063e-01,  5.0389e-01,  3.0962e-01, -1.5669e-01,
           5.1920e-01, -2.6332e-01,  4.5155e-01, -1.4681e+00,  7.8669e-01,
           1.7746e-01, -1.3134e-01,  4.5164e-01, -3.5953e-01, -7.8276e-01,
          -5.1442e-01,  1.6820e-01,  1.1237e-01,  1.7784e-01, -9.7738e-01,
           6.3420e-01,  8.1225e-01,  7.2917e-02,  5.0084e-01,  6.9180e-02,
          -5.3283e-01,  1.7649e-01, -3.7593e-02, -8.8134e-01,  3.7394e-01,
           2.7871e-01,  9.7662e-02,  2.3348e-01,  1.2168e-01,  1.0648e+00,
           3.3742e-01, -1.5237e-01,  7.6630e-01, -2.3264e-01,  9.6966e-02,
          -4.8706e-01, -4.0664e-01,  7.1880e-01, -1.2844e-01,  7.2659e-01,
           2.4798e-01,  1

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[104]]), pad_token_id=103, bos_token_id=105,eos_token_id=102, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[104,  32,  89,  89,  56,  84,  86,  56,  12,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  60,  25],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  56],
        [104,  32,  89,  89,  56,  84,  86,  56,  46,  79],
        [104,  32,  89,  89,  56,  84,  86,  56,  12,  84]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("retrieval 18 27 5 5[SEP]")

{'input_ids': [101, 18, 27, 5, 5, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
print(decode_tokenizer.encode('18 27 5 5[SEP]'))

[104, 18, 27, 5, 5, 102]


In [ ]:
text_decoder.generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 104,
  "eos_token_id": 102,
  "pad_token_id": 103,
  "transformers_version": "4.30.2"
}

In [ ]:
checkpoint = torch.load('./mscoco.pth')

In [ ]:
for key in checkpoint.keys():
    print(key)

temp
visual_encoder.cls_token
visual_encoder.pos_embed
visual_encoder.patch_embed.proj.weight
visual_encoder.patch_embed.proj.bias
visual_encoder.blocks.0.norm1.weight
visual_encoder.blocks.0.norm1.bias
visual_encoder.blocks.0.attn.qkv.weight
visual_encoder.blocks.0.attn.qkv.bias
visual_encoder.blocks.0.attn.proj.weight
visual_encoder.blocks.0.attn.proj.bias
visual_encoder.blocks.0.norm2.weight
visual_encoder.blocks.0.norm2.bias
visual_encoder.blocks.0.mlp.fc1.weight
visual_encoder.blocks.0.mlp.fc1.bias
visual_encoder.blocks.0.mlp.fc2.weight
visual_encoder.blocks.0.mlp.fc2.bias
visual_encoder.blocks.1.norm1.weight
visual_encoder.blocks.1.norm1.bias
visual_encoder.blocks.1.attn.qkv.weight
visual_encoder.blocks.1.attn.qkv.bias
visual_encoder.blocks.1.attn.proj.weight
visual_encoder.blocks.1.attn.proj.bias
visual_encoder.blocks.1.norm2.weight
visual_encoder.blocks.1.norm2.bias
visual_encoder.blocks.1.mlp.fc1.weight
visual_encoder.blocks.1.mlp.fc1.bias
visual_encoder.blocks.1.mlp.fc2.weigh

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
pretrained_weights = BertLMHeadModel.from_pretrained("bert-base-uncased", config=config_decoder).state_dict()
config_decoder.vocab_size = 14

model = BertLMHeadModel(config_decoder)
# pretrained_weights = BertLMHeadModel.from_pretrained(text_decoder).state_dict()
new_weights = {k: v for k, v in pretrained_weights.items() if "embeddings" not in k and model.state_dict()[k].shape == v.shape}
model.load_state_dict(new_weights, strict=False)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(


In [ ]:
tokenizer('[CLS] 1 3')

{'input_ids': [12, 12, 1, 3], 'token_type_ids': [0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1]}

In [ ]:
from models.text_encoder import BertModel
from models.image_encoder import VisionTransformer
import torch.nn as nn
from functools import partial
from torchvision import transforms
import os
from PIL import Image
import torch

encode_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
bert_config = BertConfig.from_json_file('./configs/config_bert.json')
text_encoder = BertModel.from_pretrained("bert-base-uncased", config=bert_config, add_pooling_layer=False)

   
caption = 'A man wearing a net on her head cutting a cake. '
text = encode_tokenizer(caption, padding='longest', max_length=30, return_tensors="pt")
text_output = text_encoder(text.input_ids, attention_mask = text.attention_mask,                      
                                        return_dict = True, mode = 'text') 


text_embeds = text_output.last_hidden_state
# output_pos = text_encoder(encoder_embeds = text_embeds, 
#                                         attention_mask = text.attention_mask,
#                                         encoder_hidden_states = image_embeds,
#                                         encoder_attention_mask = image_atts,      
#                                         return_dict = True,
#                                         mode = 'fusion',
#                                        )

caption_id = '0 1 8 7 9 [SEP]'
text_id = decode_tokenizer(caption_id, padding='longest', max_length=30, return_tensors="pt")
text_id_targets = text_id.input_ids.masked_fill(text_id.input_ids == decode_tokenizer.pad_token_id, -100)
text_id_output = text_decoder(text_id.input_ids,
                                        attention_mask = text_id.attention_mask, 
                                        encoder_hidden_states = text_embeds,
                                        encoder_attention_mask = text.attention_mask,                  
                                        labels = text_id_targets,
                                        return_dict = True,   
                                        reduction = 'none',
                                        ) 

/home/ubuntu/.local/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [ ]:
text_id_output.logits


tensor([[[ 2.7933e-01, -1.9018e+00,  2.4747e+00,  6.2958e-01,  1.2983e+00,
           8.9294e-01,  4.6506e-02,  5.0827e-01,  5.3826e-01, -5.7398e-02,
           7.8143e-01, -2.7243e-01,  9.1946e-01, -5.2369e-01],
         [ 2.1149e-01, -7.6190e-01,  1.1796e+00,  1.7546e+00, -1.4712e+00,
           1.0065e-02, -5.5632e-01, -5.6666e-01,  2.0187e+00, -6.2714e-01,
           7.0484e-01,  4.1383e-01,  1.0061e+00, -5.7677e-01],
         [-2.0148e-01,  5.1820e-01,  1.8035e+00,  4.7172e-01, -8.7020e-01,
          -1.7338e+00, -1.0279e+00, -1.4032e+00,  6.7546e-01, -1.1182e+00,
           6.5535e-01,  8.9059e-01,  9.4967e-01,  1.1747e-01],
         [-1.2718e+00,  1.1853e+00,  2.0647e-01,  1.9201e+00, -5.4053e-01,
          -1.0218e+00, -9.9729e-01,  3.4465e-01,  1.9729e+00, -7.1913e-01,
           6.6800e-01,  2.7557e+00,  2.9276e-01, -3.6482e-01],
         [-1.5075e+00, -1.3768e+00,  1.2271e+00,  9.8828e-01,  1.4520e+00,
           2.6608e-01, -2.5972e-01,  1.0761e+00,  6.8067e-01, -8.7997e-02

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
outputs = text_decoder.generate(inputs=torch.LongTensor([[12]]), pad_token_id=11, bos_token_id=12,eos_token_id=10, num_return_sequences=5 ,
                      max_length=10, num_beams=5, encoder_hidden_states = text_embeds, encoder_attention_mask = text.attention_mask, )

In [ ]:
outputs

tensor([[12,  2,  2,  2,  2,  2,  2,  2,  2,  2],
        [12,  2,  2,  2,  2,  2,  2,  2,  2,  5],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  3],
        [12,  2,  2,  2,  2,  2,  2,  2,  3,  2],
        [12,  2,  2,  2,  2,  2,  3,  3,  3,  3]])

In [ ]:
output = tokenizer('hello, world')
output.input_ids

[101, 7592, 1010, 2088, 102]

In [ ]:
from models.tokenizer import BertTokenizer
my_tkn = BertTokenizer.from_pretrained("bert-base-uncased")
input_id = my_tkn(['0 1 4 6 7 6 7 [SEP]','0 9 8 7'], padding='longest',return_tensors='pt')
print(input_id)

{'input_ids': tensor([[ 101, 1014, 1015, 1018, 1020, 1021, 1020, 1021,  102],
        [ 101, 1014, 1023, 1022, 1021,    0,    0,    0,    0]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1, 0, 0, 0, 0]])}


In [ ]:
from models.tokenizer import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
import torch
checkpoint = torch.load('./ALBEF.pth', map_location='cpu')

In [ ]:
for key in checkpoint['model'].keys():
    print(key)

In [ ]:
decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
decode_tokenizer("14 3 33 2")

{'input_ids': [104, 14, 3, 33, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1]}

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 102, 103, 104, 105]

In [ ]:
len(decode_tokenizer.vocab)

102

In [ ]:
a = list('1 2 3')
a

['1', ' ', '2', ' ', '3']

In [ ]:
import json
import os
from torch.utils.data import Dataset
from pycocotools.coco import COCO

In [ ]:
import torch

In [ ]:
position_ids_l = torch.arange(5, dtype=torch.long, ).view(-1, 1)
position_ids_r = torch.arange(5, dtype=torch.long, ).view(1, -1)
print(position_ids_l)
print(position_ids_r)

distance = position_ids_l - position_ids_r
print(distance + 4)


tensor([[0],
        [1],
        [2],
        [3],
        [4]])
tensor([[0, 1, 2, 3, 4]])
tensor([[4, 3, 2, 1, 0],
        [5, 4, 3, 2, 1],
        [6, 5, 4, 3, 2],
        [7, 6, 5, 4, 3],
        [8, 7, 6, 5, 4]])


In [ ]:
with open("../data/annotations/coco_train.json", 'r') as file:
    ann = json.load(file)
    print(ann[9])
    # print(ann['annotations'][0])
    # print(ann['images'][0])
    # print(len(ann['images']))



{'caption': 'a young kid with head phones on using a computer ', 'image': 'val2014/COCO_val2014_000000318219.jpg', 'image_id': 'coco_318219'}


In [ ]:
from PIL import Image
# image = Image.open('../data/val2014/COCO_val2014_000000252074.jpg').convert('RGB') 


True

In [ ]:
annFile = '../data/annotations/captions_train2014.json'
coco = COCO(annFile)
img = coco.loadImgs(318556)
print(img)

loading annotations into memory...
Done (t=0.27s)
creating index...
index created!
[{'license': 1, 'file_name': 'COCO_train2014_000000318556.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000318556.jpg', 'height': 640, 'width': 480, 'date_captured': '2013-11-15 05:00:35', 'flickr_url': 'http://farm4.staticflickr.com/3133/3378902101_3c9fa16b84_z.jpg', 'id': 318556}]


In [ ]:
from transformers import BertConfig
from transformers import ViTModel, ViTConfig
# 创建默认的BertConfig
config = ViTConfig()

# 打印配置参数
print(config)


ViTConfig {
  "attention_probs_dropout_prob": 0.0,
  "encoder_stride": 16,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.0,
  "hidden_size": 768,
  "image_size": 224,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "model_type": "vit",
  "num_attention_heads": 12,
  "num_channels": 3,
  "num_hidden_layers": 12,
  "patch_size": 16,
  "qkv_bias": true,
  "transformers_version": "4.31.0"
}



In [ ]:
from transformers import T5Tokenizer

tkn = T5Tokenizer.from_pretrained("t5-small")
tkn('134')

You are using the legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565


{'input_ids': [3, 23747, 1], 'attention_mask': [1, 1, 1]}

In [ ]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")


In [ ]:
encoded = tokenizer("Hello, my dog is cute")
print(tokenizer.decode(encoded['input_ids']))
tokenizer.tokenize("Hello, my dog is cute")

[CLS] hello, my dog is cute [SEP]


['hello', ',', 'my', 'dog', 'is', 'cute']

In [ ]:
tkn.tokenize("Hello, my dog is cute")

['▁Hello', ',', '▁my', '▁dog', '▁is', '▁cute']

In [ ]:
from models.tokenizer import BertTokenizer
tkn = BertTokenizer.from_pretrained("bert-base-uncased")

/usr/bin/python3


In [ ]:
encoded_input = tkn( "Hello, my dog is cute", add_special_tokens=True)
print(tkn.decode(encoded_input['input_ids']))

In [ ]:
sentences = ["Hello, my dog is cute", "I like to read books", "How are you?"]
tokenized_outputs = tokenizer(sentences, padding='longest', max_length=30)
print(tokenized_outputs)

{'input_ids': [[101, 7592, 1010, 2026, 3899, 2003, 10140], [101, 1045, 2066, 2000, 3191, 2808, 0], [101, 2129, 2024, 2017, 1029, 0, 0]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 0], [1, 1, 1, 1, 1, 0, 0]]}


In [ ]:
from models.decoder import BertLMHeadModel
from models.tokenizer import BertTokenizer
from transformers import BertConfig

config_decoder = BertConfig.from_json_file('./configs/config_bert_decode.json')
config_decoder.fusion_layer = 0
config_decoder.num_hidden_layers = 6
model = BertLMHeadModel(config_decoder)
text_decoder = model

decode_tokenizer = BertTokenizer.from_pretrained('./data/id_vocab.txt')

In [ ]:
from models.dec_tokenizer import Dec_Tokenizer
decode_tokenizer = Dec_Tokenizer.from_pretrained('./data/id_vocab.txt')

/home/ubuntu/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:1727: FutureWarning: Calling Dec_Tokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
text_decoder.config

NameError: name 'text_decoder' is not defined

In [ ]:
decode_tokenizer.all_special_tokens

['[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
decode_tokenizer.all_special_ids

[None, 302, 303, 304, 305]